# Export for picking

export the decoded spots for chromosome picking

In [1]:
import sys
sys.path.append(r"C:\Users\cosmosyw\Documents\Softwares")
import os

import ImageAnalysis3 as ia
%matplotlib notebook

from ImageAnalysis3 import *
print(os.getpid())

import h5py
from ImageAnalysis3.classes import _allowed_kwds
import ast

import pandas as pd
import numpy as np

import matplotlib.pyplot as plt

25444


# Exporting dataset for jie (chromosome fiber picking)

In [6]:
from ImageAnalysis3.classes.picker import SpotPicker
from tqdm import tqdm
import re
##################### Manual change #########################################
save_folder = r'E:\DNA_analysis\20220819_Mecp2_DNA_from_0809'

sel_exp = '0809'

preprocess_folder = r'Z:\Cosmos_DNA\MeC2_0809_DNA_preprocessed'
##################### Manual change #########################################

analysis_folder = os.path.join(save_folder, 'Analysis_0508')
decoder_folder = os.path.join(analysis_folder, 'Decoder')
decoder_file_regex = r'Decoded_fov-(?P<fovId>[0-9]+)_cell-(?P<cellId>[0-9]+).hdf5'
decoder_filenames = [os.path.join(decoder_folder, _fl) for _fl in tqdm(os.listdir(decoder_folder)) 
                     if re.search(decoder_file_regex, _fl) is not None
                    ]
# sort
decoder_filenames = [_fl for _fl in sorted(decoder_filenames,
                                          key=lambda _fl: (int(re.search(decoder_file_regex, _fl).groupdict()['fovId']), 
                                           int(re.search(decoder_file_regex, _fl).groupdict()['cellId'])) )
                    ]

100%|████████████████████████████████████████████████████████████████████████| 41914/41914 [00:00<00:00, 278890.12it/s]


In [7]:
#export_folder = r'\\10.245.74.158\Chromatin_NAS_8\Exported_data\20220316-Export_new_v2'
export_folder = os.path.join(analysis_folder, 'Exported_hdf5')
if not os.path.exists(export_folder):
    os.makedirs(export_folder)
    print(f"Creating export_folder: {export_folder}")
else:
    print(f"Use export_folder: {export_folder}")

Use export_folder: E:\DNA_analysis\20220819_Mecp2_DNA_from_0809\Analysis_0508\Exported_hdf5


## Load dict from fovCellId_2_class

In [8]:
save_filenames = [os.path.join(preprocess_folder, _fl) for _fl in os.listdir(preprocess_folder)
                  if _fl.split(os.extsep)[-1]=='hdf5']

# extract fov_id
save_fov_ids = [int(os.path.basename(_fl).split('.hdf5')[0].split('_')[-1]) for _fl in save_filenames]
print(f"{len(save_filenames)} fovs detected")

243 fovs detected


In [9]:
%%time
segmentation_folder = os.path.join(analysis_folder, 'Segmentation')
fovcell_2_uid = {}
for _fov_id, _save_filename in zip(save_fov_ids, save_filenames):
    # segmentation filename
    _segmentation_savefile = os.path.join(segmentation_folder, 
        os.path.basename(_save_filename).replace('.hdf5', '_Segmentation.hdf5') )
    
    with h5py.File(_segmentation_savefile, 'r') as _f:
        for _fov_id in _f.keys():
            _fov_group = _f[_fov_id]
            _uid_group = _fov_group['cell_2_uid']
            for _cell_id in _uid_group.keys():
                fovcell_2_uid[(_fov_id, _cell_id)] = _uid_group[_cell_id][:][0].decode()

CPU times: total: 7.16 s
Wall time: 12.2 s


In [10]:
fovcell_2_uid.keys()
fovcell_2_uid[('1', '1')]

'124558108717070871741415336417553674419'

In [11]:
import scanpy as sc
# load cell type info
merfish_cluster_file = r"C:\Users\cosmosyw\Documents\Research\Mecp2_v2\results\adata\MeCP2_clustered_adata_labeled.h5ad"
merfish_df = sc.read_h5ad(merfish_cluster_file)
print(len(merfish_df))
#print(np.unique(merfish_df.obs['experiment']) )

152286


In [12]:
print(merfish_df.obs.columns)
experiment_col_name = 'experiment'
print(np.unique(merfish_df.obs[experiment_col_name]) )

Index(['fov', 'volume', 'center_x', 'center_y', 'min_x', 'max_x', 'min_y',
       'max_y', 'experiment', 'mouse', 'age', 'n_genes_by_counts',
       'total_counts', 'leiden', 'subclass_prediction_label',
       'leiden_subclass_sub', 'subclass_manual_label',
       'subclass_prediction_label_2'],
      dtype='object')
['0722' '0724' '0808' '0809' '1027' '1029' '1101' '1103' '1105' '1107']


In [13]:
%matplotlib inline
sc.pl.umap(merfish_df,color='subclass_manual_label', legend_loc='on data')

In [14]:
# load specifically this experiment
sel_obs = merfish_df.obs.loc[merfish_df.obs[experiment_col_name]==sel_exp]
uid_2_class = {_uid:_class for _uid, _class in zip(sel_obs.index, sel_obs['subclass_manual_label'])}
print(len(uid_2_class))
# assemble fovcell_2_class dict
fovcell_2_class = {}
for _decoder_fl in tqdm(decoder_filenames):
    _reg_match = re.search(decoder_file_regex, _decoder_fl)
    _fov_id, _cell_id = _reg_match.groupdict()['fovId'], _reg_match.groupdict()['cellId']
    if (_fov_id, _cell_id) in fovcell_2_uid:
        #print('cell exists')
        _uid = fovcell_2_uid[ (_fov_id, _cell_id) ]
        if _uid in uid_2_class:
            fovcell_2_class[(_fov_id, _cell_id)] = uid_2_class[_uid]
            #print('found cell subclass info')
        else:
            fovcell_2_class[(_fov_id, _cell_id)] = 'other'
print(len(fovcell_2_class))

16574


100%|████████████████████████████████████████████████████████████████████████| 14031/14031 [00:00<00:00, 596568.40it/s]

14031


In [15]:
np.unique(list(fovcell_2_class.values()),return_counts=True)

# these many other cells are presumbaly the ones filtered during scanpy preprocessing

(array(['Astro', 'Endo-PVM', 'L2/3 IT', 'L4/5 IT', 'L5 ET', 'L5 IT',
        'L5/6 NP', 'L6 CT', 'L6 IT', 'L6b', 'Lamp5', 'Micro', 'OPC',
        'Oligo', 'Peri', 'Pvalb', 'SMC-VLMC', 'Sncg', 'Sst', 'Vip'],
       dtype='<U8'),
 array([1335, 1026, 1357,  720,  370,  893,  243, 2161,  983,  290,  155,
         308,  333, 2156,  364,  490,  197,   88,  386,  176], dtype=int64))

## Export

In [16]:
min_decoded_num = 20

for _decoder_fl in tqdm(decoder_filenames):
    _reg_match = re.search(decoder_file_regex, _decoder_fl)
    _fov_id, _cell_id = _reg_match.groupdict()['fovId'], _reg_match.groupdict()['cellId']
    # skip other
    if fovcell_2_class[(_fov_id, _cell_id)] == 'other':
        continue
    # export info
    export_filename = os.path.join(export_folder, f"Decoded_Fov-{_fov_id}.hdf5")
    #if os.path.exists(export_filename) and f"Cell-{_cell_id}" in h5py.File(export_filename).keys():
    #    continue

    
    # load
    _cls = SpotPicker(_decoder_fl, verbose=False, save_file=None)
    _cls._load_decoded()
    _cls._merge_decoded()
    if not hasattr(_cls, 'merged_coords'):
        continue
    # save
    if len(_cls.merged_coords) > min_decoded_num:
        _cls.merged_coords['subclass'] = fovcell_2_class[(_fov_id, _cell_id)]
        _cls.merged_coords.to_hdf(export_filename, f"Cell-{_cell_id}")


  0%|                                                                                        | 0/14031 [00:00<?, ?it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-1'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*`; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
  0%|                                                                                | 1/14031 [00:00<54:17,  4.31it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-2'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
  0%|                           

  0%|                                                                             | 17/14031 [00:04<1:06:08,  3.53it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-21'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
  0%|                                                                             | 18/14031 [00:05<1:04:45,  3.61it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-27'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*  0%|                                                                             | 17/14031 [00:04<1:06:08,  3.53it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\

  0%|▏                                                                              | 33/14031 [00:09<58:12,  4.01it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-52'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*`; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
  0%|▏                                                                            | 34/14031 [00:09<1:03:24,  3.68it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-55'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
  0%|▏                        

  0%|▎                                                                            | 50/14031 [00:14<1:05:19,  3.57it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-16'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
  0%|▎                                                                            | 51/14031 [00:14<1:02:10,  3.75it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-18'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*  0%|▎                                                                            | 50/14031 [00:14<1:05:19,  3.57it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\

  0%|▎                                                                              | 66/14031 [00:18<56:25,  4.13it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-35'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
  0%|▍                                                                              | 67/14031 [00:18<57:00,  4.08it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-37'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*  0%|▎                                                                              | 66/14031 [00:18<56:25,  4.13it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\

...

 99%|█████████████████████████████████████████████████████████████████████████▌| 13952/14031 [1:00:53<00:26,  2.93it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-49'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
 99%|█████████████████████████████████████████████████████████████████████████▌| 13953/14031 [1:00:53<00:26,  2.96it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-50'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]* 99%|█████████████████████████████████████████████████████████████████████████▌| 13952/14031 [1:00:53<00:26,  2.93it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\

100%|█████████████████████████████████████████████████████████████████████████▋| 13968/14031 [1:00:59<00:20,  3.05it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-72'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
100%|█████████████████████████████████████████████████████████████████████████▋| 13969/14031 [1:00:59<00:21,  2.91it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-73'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*100%|█████████████████████████████████████████████████████████████████████████▋| 13968/14031 [1:00:59<00:20,  3.05it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\

100%|█████████████████████████████████████████████████████████████████████████▊| 13984/14031 [1:01:03<00:11,  4.17it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-5'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
100%|█████████████████████████████████████████████████████████████████████████▊| 13985/14031 [1:01:03<00:11,  3.85it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-7'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*100%|█████████████████████████████████████████████████████████████████████████▊| 13984/14031 [1:01:03<00:11,  4.17it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\li

100%|█████████████████████████████████████████████████████████████████████████▊| 14000/14031 [1:01:07<00:08,  3.49it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-37'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
100%|█████████████████████████████████████████████████████████████████████████▊| 14001/14031 [1:01:08<00:08,  3.44it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-39'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*100%|█████████████████████████████████████████████████████████████████████████▊| 14000/14031 [1:01:07<00:08,  3.49it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\

100%|█████████████████████████████████████████████████████████████████████████▉| 14016/14031 [1:01:13<00:05,  2.82it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-73'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
100%|█████████████████████████████████████████████████████████████████████████▉| 14017/14031 [1:01:13<00:04,  2.93it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\lib\site-packages\tables\path.py:155: NaturalNameWarning: object name is not a valid Python identifier: 'Cell-75'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*100%|█████████████████████████████████████████████████████████████████████████▉| 14016/14031 [1:01:13<00:05,  2.82it/s]C:\Users\cosmosyw\anaconda3\envs\merlin_postanalysis\